In [ ]:
# --------------------------------------------------------------
# Google Colab: Convert a folder of PDFs → 1256×1256 PNGs
# --------------------------------------------------------------

# 1. Install required libraries
!apt-get -qq update
!apt-get -qq install -y poppler-utils   # provides pdftoppm
!pip install -q pdf2image tqdm

# 2. Import modules
import os
from pathlib import Path
from pdf2image import convert_from_path
from PIL import Image
from tqdm import tqdm
import zipfile
import shutil

# --------------------------------------------------------------
# 3. Choose source: upload files OR mount Google Drive
# --------------------------------------------------------------
USE_DRIVE = True  # Set True to read PDFs from Drive

if USE_DRIVE:
    from google.colab import drive
    drive.mount('/content/drive')
    pdf_dir = Path('/content/drive/MyDrive/PDFs')   # <-- change to your folder
else:
    from google.colab import files
    uploaded = files.upload()   # <-- upload PDFs here
    pdf_dir = Path('/content/uploaded_pdfs')
    pdf_dir.mkdir(exist_ok=True)
    for name, data in uploaded.items():
        (pdf_dir / name).write_bytes(data)

# --------------------------------------------------------------
# 4. Output folder & zip
# --------------------------------------------------------------
out_dir = Path('/content/png_output')
out_dir.mkdir(exist_ok=True)

zip_path = '/content/pdf_pngs_1256x1256.zip'

# --------------------------------------------------------------
# 5. Conversion function
# --------------------------------------------------------------
def pdf_to_1256_png(pdf_path: Path, out_dir: Path):
    """
    Convert each page of a PDF into a 1256×1256 PNG.
    The page is scaled to fit inside the square while keeping aspect ratio.
    """
    # Convert PDF pages to PIL images (dpi≈300 → good quality)
    pages = convert_from_path(str(pdf_path), dpi=500)

    base_name = pdf_path.stem
    for i, page in enumerate(pages, start=1):
        # Create a 1556×1556 white canvas
        canvas = Image.new('RGB', (1556, 1556), (255, 255, 255))

        # Compute scaling to fit the page inside the canvas
        page_ratio = page.width / page.height
        target_ratio = 1556 / 1556

        if page_ratio > target_ratio:
            # fit width
            new_w = 1556
            new_h = int(1556 / page_ratio)
        else:
            # fit height
            new_h = 1556
            new_w = int(1556 * page_ratio)

        resized = page.resize((new_w, new_h), Image.LANCZOS)

        # Center the resized image on the canvas
        offset = ((1556 - new_w) // 2, (1556 - new_h) // 2)
        canvas.paste(resized, offset)

        # Save
        png_name = f"{base_name}_page{i:03d}.png"
        canvas.save(out_dir / png_name, 'PNG')
    return len(pages)

# --------------------------------------------------------------
# 6. Run conversion for all PDFs
# --------------------------------------------------------------
pdf_files = list(pdf_dir.glob('*.pdf'))
if not pdf_files:
    raise FileNotFoundError("No PDF files found in the selected folder.")

total_pages = 0
for pdf_path in tqdm(pdf_files, desc="Converting PDFs"):
    total_pages += pdf_to_1256_png(pdf_path, out_dir)

print(f"\nDone! Converted {len(pdf_files)} PDFs → {total_pages} PNGs")
print(f"PNG folder: {out_dir}")

# --------------------------------------------------------------
# 7. Zip & download
# --------------------------------------------------------------
print("Creating zip archive...")
with zipfile.ZipFile(zip_path, 'w', zipfile.ZIP_DEFLATED) as z:
    for png_file in out_dir.rglob('*.png'):
        z.write(png_file, arcname=png_file.relative_to(out_dir.parent))

print(f"Zip ready: {zip_path}")
#files.download(zip_path)

In [ ]:
# Install required libraries
#!pip install pillow google-colab

from google.colab import drive
from PIL import Image
import os
import zipfile
from pathlib import Path
import shutil

# Mount Google Drive
drive.mount('/content/drive')

# Define paths and settings
source_dir = '/content/drive/MyDrive/Saved from Chrome/'
output_zip = '/content/images_lossless_1024_webp.zip'
webp_dir = '/content/temp_lossless_1024_webp'
MAX_SIZE = 1024  # Maximum dimension (width or height)

# Create temporary directory for resized lossless webp files
os.makedirs(webp_dir, exist_ok=True)

# Get all image files
image_extensions = {'.jpg', '.jpeg', '.png', '.bmp', '.tiff', '.gif', '.webp'}
image_files = []

print("🔍 Scanning for images...")
for file_path in Path(source_dir).rglob('*'):
    if file_path.is_file() and file_path.suffix.lower() in image_extensions:
        image_files.append(file_path)

print(f"✅ Found {len(image_files)} image files")

# Convert, resize, and save as lossless WebP
webp_files = []
failed_conversions = []
resize_stats = {'resized': 0, 'unchanged': 0}

print("🔄 Resizing to 1024px max dimension & converting to lossless WebP...")
for i, img_path in enumerate(image_files, 1):
    try:
        # Open image
        with Image.open(img_path) as img:
            original_width, original_height = img.size

            # Resize if either dimension exceeds MAX_SIZE
            if original_width > MAX_SIZE or original_height > MAX_SIZE:
                # Calculate scaling factor to fit within MAX_SIZE
                scale = min(MAX_SIZE / original_width, MAX_SIZE / original_height)
                new_width = int(original_width * scale)
                new_height = int(original_height * scale)

                # Resize using high-quality LANCZOS resampling
                img_resized = img.resize((new_width, new_height), Image.Resampling.LANCZOS)
                resize_stats['resized'] += 1
            else:
                img_resized = img
                resize_stats['unchanged'] += 1

            # Preserve original mode (including transparency) for lossless conversion
            # Save as lossless WebP
            webp_path = os.path.join(webp_dir, f"{i:04d}.webp")
            img_resized.save(webp_path, 'WEBP', lossless=True, method=6)
            webp_files.append(webp_path)

        if i % 10 == 0 or i == len(image_files):
            print(f"  Processed {i}/{len(image_files)} images")

    except Exception as e:
        error_msg = f"Error processing {img_path.name}: {str(e)}"
        print(f"❌ {error_msg}")
        failed_conversions.append((img_path, str(e)))
        continue

print(f"\n📏 Resize Statistics:")
print(f"   Images resized: {resize_stats['resized']}")
print(f"   Images unchanged: {resize_stats['unchanged']}")
print(f"✅ Successfully converted {len(webp_files)} images to 1024px lossless WebP")

# Create zip file with maximum compression
print("📦 Creating ZIP archive...")
with zipfile.ZipFile(output_zip, 'w', zipfile.ZIP_DEFLATED, compresslevel=9) as zipf:
    for webp_file in webp_files:
        arcname = os.path.basename(webp_file)
        zipf.write(webp_file, arcname)
        if len(webp_files) <= 20 or webp_files.index(webp_file) % 20 == 0:
            print(f"  Added {arcname}")

# Calculate statistics
original_size = sum(os.path.getsize(f) for f in image_files)
webp_size = sum(os.path.getsize(f) for f in webp_files)
zip_size = os.path.getsize(output_zip)

size_reduction = (1 - webp_size/original_size) * 100 if original_size > 0 else 0

print(f"\n📊 Conversion Statistics:")
print(f"   Original images size:    {original_size / (1024*1024):.2f} MB")
print(f"   1024px Lossless WebP:    {webp_size / (1024*1024):.2f} MB")
print(f"   Size reduction:          {size_reduction:.1f}%")
print(f"   Final ZIP size:          {zip_size / (1024*1024):.2f} MB")

# Copy zip back to Google Drive
drive_output = '/content/drive/MyDrive/images_1024_lossless_webp.zip'
shutil.copy2(output_zip, drive_output)
print(f"💾 ZIP saved to Google Drive: {drive_output}")

# Clean up temporary directory
shutil.rmtree(webp_dir)
print("🧹 Temporary files cleaned up")

# Display sample of files in zip
print("\n📋 Sample files in ZIP:")
with zipfile.ZipFile(output_zip, 'r') as zipf:
    file_list = zipf.namelist()
    for i, filename in enumerate(file_list[:10], 1):
        print(f"   {i}. {filename}")
    if len(file_list) > 10:
        print(f"   ... and {len(file_list) - 10} more files")

print(f"\n🎯 AI-Training Ready (1024px Optimized)!")
print(f"   • ✅ 1024px max resolution - standardized for ML")
print(f"   • ✅ 100% lossless quality - NO compression artifacts")
print(f"   • ✅ Preserves transparency (RGBA support)")
print(f"   • ✅ High-quality LANCZOS resampling")
print(f"   • ✅ Sequential numbering: 0001.webp, 0002.webp, etc.")
print(f"   • 🎯 Perfect for CNNs, GANs, object detection, segmentation")
print(f"   • ⚡ Consistent input size for faster training")
print(f"   • 💾 Significant storage savings vs original high-res images")

if failed_conversions:
    print(f"\n⚠️  Failed conversions (check originals):")
    for orig_path, error in failed_conversions[:5]:
        print(f"   • {orig_path.name}: {error}")
    if len(failed_conversions) > 5:
        print(f"   ... and {len(failed_conversions) - 5} more")

print(f"\n🔧 Technical Details:")
print(f"   • Max dimension: {MAX_SIZE}px (maintains aspect ratio)")
print(f"   • Resampling: LANCZOS (highest quality)")
print(f"   • Lossless WebP: Perfect fidelity, ~50% smaller than PNG")

# 📸 Google Drive Image Converter to WebP

**Convert your Chrome-saved images to compact WebP format with automatic indexing!**

This Google Colab notebook transforms all images from your `MyDrive/Saved from Chrome/` folder into optimized WebP files, named sequentially as `1.webp`, `2.webp`, `3.webp`, etc., and packages them into a single ZIP archive.

## ✨ Features
- **Batch Processing**: Automatically finds and converts JPG, PNG, GIF, BMP, TIFF, and existing WebP files
- **Smart Conversion**: Handles transparency by converting RGBA/P modes to RGB with white background
- **High-Quality WebP**: Uses 85% quality setting for optimal size/quality balance
- **Recursive Search**: Processes images in subfolders too
- **Error-Resilient**: Skips corrupt files and continues processing
- **Dual Output**: Saves ZIP locally in Colab AND copies to your Google Drive root
- **Progress Tracking**: Shows conversion progress and final statistics

## 🚀 How It Works
1. Mounts your Google Drive
2. Scans for image files in "Saved from Chrome/" and subdirectories
3. Converts each image to WebP with sequential numbering
4. Creates a compressed ZIP archive
5. Cleans up temporary files and reports file sizes

## 💾 Output
- `images_webp.zip` containing `1.webp`, `2.webp`, `3.webp`, etc.
- Significantly smaller file sizes (WebP compression typically 25-35% better than JPEG)
- Ready for web use, storage, or sharing

## 🎯 Perfect For
- Organizing Chrome download clutter
- Web developers needing optimized images
- Anyone wanting to save Google Drive storage space
- Creating indexed image collections for ML datasets or galleries

**Run this notebook to instantly compress and organize your Chrome-saved images into a clean, numbered WebP collection!**

*Note: Requires Google Drive authentication when first run.*